In [1]:
!pip install pdfplumber langchain langchain_groq

  Using cached pdfplumber-0.11.6-py3-none-any.whl.metadata (42 kB)
  Using cached pdfminer_six-20250327-py3-none-any.whl.metadata (4.1 kB)
  Using cached pypdfium2-4.30.1-py3-none-win_amd64.whl.metadata (48 kB)
Using cached pdfplumber-0.11.6-py3-none-any.whl (60 kB)
Using cached pdfminer_six-20250327-py3-none-any.whl (5.6 MB)
Using cached pypdfium2-4.30.1-py3-none-win_amd64.whl (3.0 MB)


In [2]:
import os
import pdfplumber
import json

def extract_text_from_pdf(pdf_path, pages_per_doc=5):
    with pdfplumber.open(pdf_path) as pdf:
        all_pages = [page.extract_text() for page in pdf.pages]

    # Split pages into chunks of 5
    chunks = []
    for i in range(0, len(all_pages), pages_per_doc):
        chunk = all_pages[i:i+pages_per_doc]
        chunks.append(" ".join(chunk))

    return chunks

pdf_folder = "C:/Users/TANAY/Python_project/IRGANs/document_base-cows"
documents = {}

for filename in os.listdir(pdf_folder):
    if filename.endswith(".pdf"):
        base_id = filename.split(".")[0]
        pdf_path = os.path.join(pdf_folder, filename)

        # Get 5-page chunks
        text_chunks = extract_text_from_pdf(pdf_path)

        # Create unique IDs for each chunk
        for chunk_idx, chunk_text in enumerate(text_chunks):
            doc_id = f"{base_id}_part{chunk_idx}"
            documents[doc_id] = chunk_text

# Save to JSON
with open("documents.json", "w") as f:
    json.dump(documents, f, indent=2)

CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, defaulting to MediaBox
CropBox missing from /Page, def

In [3]:
# Save to JSON
import json
import os

with open("documents.json", "w") as f:
    json.dump(documents, f)

In [4]:
# load document.json from the files

# Check if the file exists before attempting to load it.
if os.path.exists('documents.json'):
    with open('documents.json', 'r') as f:
        try:
            data = json.load(f)
            print(data)  # Or perform other operations with the loaded data
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON: {e}")
else:
    print("documents.json file not found.")

{'compendium_part0': 'SAARC\nHerd Health Management of Dairy\nB u f f a l o\nInderjeet Singh A Bharadwaj SS Paul KP Singh RK Sharma\nICAR-Central Institute for Research on Buffaloes Training Program the for SAARC Countries on\nHerd Health Management of Dairy Buffalo :\nNutrition, Breeding, Reproduction, Diseases,\nManagement and Record Keeping\n(August 22-27, 2016)\nProgramme Director\nInderjeet Singh\nProgramme co-ordinator\nA Bhardwaj\nSS Paul\nKP Singh\nRK Sharma\nSponsored by :\nSAARC\nSAARC Agriculture Centre, Dhaka, Bangladesh\nOrganized by :\nICAR-Central Institute for Research on Buffaloes\nHisar-125 001 (Haryana) India Published by\nInderjeet Singh,\nDirector, ICAR-CIRB, Hisar, India\nCompiled and edited by\nInderjeet Singh\nA Bhardwaj\nSS Paul\nKP Singh\nRK Sharma\nCorrect citation:\nInderjeet Singh, A Bhardwaj, SS Paul, KP Singh and RK Sharma, (Eds.) 2016. Herd Health\nManagement of Dairy Buffalo : Nutrition, Breeding, Reproduction, Diseases, Management and\nRecord Keeping. 

In [5]:
from dotenv import load_dotenv
load_dotenv()
groq_api_key = os.getenv("GROQ_API_KEY")

In [ ]:
from langchain_groq import ChatGroq
from langchain_core.messages import AIMessage
import time
import random
import json


# List of available Groq models to rotate through
GROQ_MODELS = [
    "llama-3.1-8b-instant",
    "gemma2-9b-it",
    "llama-3.3-70b-versatile",
    "llama3-70b-8192"
]

# Track rate limits per model (global state)
model_rate_track = {model: {"last_call": 0, "calls": 0} for model in GROQ_MODELS}

def get_next_model():
    """Select model with oldest last call time and under rate limits"""
    now = time.time()

    # Filter models that haven't hit limits
    available_models = [
        model for model, stats in model_rate_track.items()
        if now - stats["last_call"] > 60/stats.get("rpm", 30)  # Default 30 RPM
    ]

    if not available_models:
        # All models rate limited - sleep and return random
        time.sleep(10)
        return random.choice(GROQ_MODELS)

    # Return least recently used available model
    return min(available_models, key=lambda m: model_rate_track[m]["last_call"])

def generate_queries(document_text, n=3, groq_api_key=None, max_retries=3):
    """Generate queries with model rotation and rate limit handling"""
    for attempt in range(max_retries):
        try:
            model = get_next_model()

            # Update rate tracking
            model_rate_track[model]["last_call"] = time.time()
            model_rate_track[model]["calls"] += 1

            llm = ChatGroq(
                groq_api_key=groq_api_key,
                model=model,
                temperature=0.7
            )

            response = llm.invoke(
                f"Generate exactly {n} search queries this document answers. "
                f"Return one query per line without numbering:\n{document_text[:3000]}"
            )

            if isinstance(response, AIMessage):
                content = response.content
            else:
                content = str(response)

            queries = [q.strip() for q in content.split("\n") if q.strip()]
            return queries[:n]

        except Exception as e:
            print(f"Attempt {attempt+1} failed with {model}: {str(e)[:100]}")
            time.sleep(5 * (attempt + 1))  # Exponential backoff

    return []  # Return empty if all retries fail


# Usage
query_doc_pairs = []

with open("documents.json", "r") as f:
    documents = json.load(f)

groq_api_key = os.getenv("GROQ_API_KEY")

for doc_id, text in documents.items():
    queries = generate_queries(
        document_text=text,
        n=3,
        groq_api_key=groq_api_key
    )

    if queries:
        query_doc_pairs.extend([(q, doc_id, 1) for q in queries])

    # Optional: Add small delay between calls
    time.sleep(0.5)  # Adjust based on your rate limits


In [11]:
# prompt: code to save and download query_doc_pairs

import json

# Save query_doc_pairs to a JSON file
with open("query_doc_pairs.json", "w") as f:
    json.dump(query_doc_pairs, f)

# Download the JSON file
# from google.colab import files
# files.download("query_doc_pairs.json")


In [12]:
query_doc_pairs

[['SAARC training programs on dairy buffalo health management',
  'compendium_part0',
  1],
 ['ICAR-Central Institute for Research on Buffaloes training programs',
  'compendium_part0',
  1],
 ['International training program on herd health management of dairy buffalo',
  'compendium_part0',
  1],
 ['ICAR-Institute for Research on Buffaloes, Hisar, Haryana, India',
  'compendium_part1',
  1],
 ['SAARC sponsored International Training programme on “Herd Health Management of Dairy Buffalo”',
  'compendium_part1',
  1],
 ['SAARC livestock production and food security', 'compendium_part1', 1],
 ['Buffalo research and development in India', 'compendium_part2', 1],
 ['Indian government initiatives for livestock productivity improvement',
  'compendium_part2',
  1],
 ['Artificial insemination programs for cattle and buffaloes in India',
  'compendium_part2',
  1],
 ['Here are three search queries that this document answers:',
  'compendium_part3',
  1],
 ['what is the role of the central inst

In [ ]:
!pip install rank_bm25

In [13]:
from rank_bm25 import BM25Okapi
import random

with open("documents.json", "r") as f:
    documents = json.load(f)

with open("query_doc_pairs.json", "r") as f:
    query_doc_pairs = json.load(f)


corpus = list(documents.values())
tokenized_corpus = [doc.split() for doc in corpus]
bm25 = BM25Okapi(tokenized_corpus)

# Step 2: For each query in `query_doc_pairs`, find hard negatives
labeled_data = []
for query, source_doc_id, relevance in query_doc_pairs:
    if relevance == 1:  # Only process positive pairs
        tokenized_query = query.split()
        scores = bm25.get_scores(tokenized_query)

        # Get top 3 relevant docs (excluding the source document)
        all_indices = list(range(len(corpus)))
        source_index = list(documents.keys()).index(source_doc_id)
        candidate_indices = [i for i in all_indices if i != source_index]

        # Sort and pick top 3 as positives (already labeled)
        sorted_indices = sorted(candidate_indices, key=lambda i: -scores[i])
        top_doc_indices = sorted_indices[:3]

        # Add existing positive labels (from `query_doc_pairs`)
        labeled_data.append((query, source_doc_id, 1))

        # Add new hard negatives (low BM25 scores)
        neg_indices = sorted_indices[-3:]  # Least relevant docs
        for idx in neg_indices:
            doc_id = list(documents.keys())[idx]
            labeled_data.append((query, doc_id, 0))


In [ ]:
labeled_data

[('Here are three search queries this document answers:',
  'https__www_part0',
  1),
 ('Here are three search queries this document answers:',
  'https__www_part243',
  0),
 ('Here are three search queries this document answers:',
  'https__www_part244',
  0),
 ('Here are three search queries this document answers:',
  'https__www_part246',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part0',
  1),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part9',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part99',
  0),
 ('Bovine medicine diseases and husbandry of cattle second edition',
  'https__www_part130',
  0),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part0',
  1),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part244',
  0),
 ('Cattle diseases and husbandry management and treatment',
  'https__www_part246

In [14]:
import json
# from google.colab import files

# Save labeled_data to a JSON file
with open("labeled_data.json", "w") as f:
    json.dump(labeled_data, f)

# # Download the JSON file
# files.download("labeled_data.json")